In [ ]:
import flatsurf

In [ ]:
S = flatsurf.translation_surfaces.octagon_and_squares().delaunay_triangulation()
S.plot(adjacencies=None)

In [ ]:
S = flatsurf.translation_surfaces.octagon_and_squares().triangulate()
S.plot(adjacencies=None)

In [ ]:
from ipymuvue.widgets import VueWidget
from traitlets import Unicode, Dict, Int, List, Float, Tuple

class Widget(VueWidget):
    def __init__(self, surface):
        super().__init__(self.template)
        
        self.surface = surface
        self.error = (-1, -1)
        self.relayout()
        
    template = r"""
    <svg :width="width" :height="height">
        <g v-for="(triangle, i) of svg_triangles" :key="label">
            <polygon :points="triangle[0][0] + ',' + triangle[0][1] + ',' + triangle[1][0] + ',' + triangle[1][1] + ',' + triangle[2][0] + ',' + triangle[2][1]"
                :fill="selected == labels[i] ? 'lavender' : 'ghostwhite'" @click="selected = labels[i]" />
            <line v-for="e of [0, 1, 2]" :key="e"
                :stroke="error[0] == i && error[1] == e ? 'red' : 'black'"
                stroke-width="2px"
                :x1="triangle[e][0]" :y1="triangle[e][1]"
                :x2="triangle[(e +1) % 3][0]" :y2="triangle[(e + 1)%3][1]"
            />
            <line v-for="e of [0, 1, 2]" :key="e" stroke="transparent" stroke-width="40px" @click="flip(i, e)"
                :x1="triangle[e][0]" :y1="triangle[e][1]"
                :x2="triangle[(e +1) % 3][0]" :y2="triangle[(e + 1)%3][1]"
            />
        </g>
    </svg>
    """

    def graphical_triangles(self):
        return [self.graphical_surface.graphical_polygon(label) for label in self.surface.labels()]

    def scale(self, xy):
        ((xmin, xmax), (ymin, ymax)) = self.bbox()
        plot_width = (xmax - xmin)
        plot_height = (ymax - ymin)
        normalized = [
            float((xy[0] - xmin) / plot_width),
            float((ymax - xy[1]) / plot_height)]
        normalized = [normalized[0] *.9 + .05, normalized[1] * .9 + .05]
        svg_coordinates = [normalized[0] * self.width, normalized[1] * self.height]
        return [float(xy) for xy in svg_coordinates]

    def relayout(self):
        self.graphical_surface = self.surface.graphical_surface()
        self.svg_triangles = [[self.scale(triangle.transformed_vertex(t)) for t in range(3)] for triangle in self.graphical_triangles()]
        self.labels = list([int(label) for label in self.surface.labels()])
        
    def bbox(self):
        xs = [triangle.xmin() for triangle in self.graphical_triangles()] + [triangle.xmax() for triangle in self.graphical_triangles()]
        ys = [triangle.ymin() for triangle in self.graphical_triangles()] + [triangle.ymax() for triangle in self.graphical_triangles()]

        return [
            [min(xs), max(xs)],
            [min(ys), max(ys)]
        ]

    @VueWidget.callback
    def flip(self, index, edge):
        label = list(self.surface.labels())[index]
        try:
            self.surface = self.surface.triangle_flip(label, edge)
        except ValueError:
            self.error = (index, edge)
        else:
            self.relayout()
            self.error = (-1, -1)

    width = Int(600R).tag(sync=True)
    height = Int(600R).tag(sync=True)

    labels = List(Int()).tag(sync=True)

    error = Tuple((-1R, -1R)).tag(sync=True)

    svg_triangles = List(List(Tuple(Float(), Float()))).tag(sync=True)

    selected = Int(-1R).tag(sync=True)


widget = Widget(S)
widget

In [ ]:
widget.selected

In [ ]:
widget.graphical_surface.plot(aspect_ratio='automatic')